Imports, global variables and SETTINGS

In [1]:
import pandas as pd
import numpy as np
import re

#pd.set_option('display.max_rows', 500)
#pd.set_option('display.max_columns', 500)
#pd.set_option('display.width', 1000)
#pd.set_option('display.max_colwidth', 1000)


filename = "file.csv"

columns_to_remove = "kolumnid.txt"

data = pd.DataFrame(pd.read_csv(filename, sep=";"))



########################################################SETTINGS########################################################

#Set true to use openstreetmaps to convert gps coordinates to addresses when the Address field is being corrected.
generate_missing_address_from_coords_online = False

#Set true to use openstreetmaps to convert addresses to gps coordinates when the GPS  fields are being corrected.
generate_missing_coords_from_address_online = True

#Set true to convert all coordinates from L-EST97 to WGS-84
do_convert_coordinates = True

########################################################################################################################

Removing columns we do not need:

In [2]:
with open(columns_to_remove, encoding = "UTF-8") as file:
    for line in file:
        var = line.strip().split("|")

        if var[2].strip() == "drop":
            data = data.drop(columns=f"{var[1].strip()}")
            print(f"[{var[0].strip()}] Column {var[1].strip()} was dropped.")
        else:
            print(f"[{var[0].strip()}] Column {var[1].strip()} was not dropped.")

[0] Column Juhtumi nr was not dropped.
[1] Column Toimumisaeg was not dropped.
[2] Column Isikuid was not dropped.
[3] Column Hukkunuid was not dropped.
[4] Column Vigastatuid was not dropped.
[5] Column Sõidukeid was not dropped.
[6] Column Aadress (PPA) was not dropped.
[7] Column Maja nr (PPA) was dropped.
[8] Column Tänav (PPA) was dropped.
[9] Column Ristuv tänav (PPA) was dropped.
[10] Column Maakond (PPA) was dropped.
[11] Column Omavalitsus (PPA) was dropped.
[12] Column Asustus (PPA) was dropped.
[13] Column Asula was dropped.
[14] Column Liiklusõnnetuse liik [1] was dropped.
[15] Column Liiklusõnnetuse liik [3] was not dropped.
[16] Column Kergliikurijuhi osalusel was not dropped.
[17] Column Jalakäija osalusel was not dropped.
[18] Column Kaassõitja osalusel was not dropped.
[19] Column Maastikusõiduki juhi osalusel was not dropped.
[20] Column Eaka (65+) mootorsõidukijuhi osalusel was not dropped.
[21] Column Bussijuhi osalusel was not dropped.
[22] Column Veoautojuhi osalu

Fixing each column in the dataset:

Fix column "Juhtumi nr"

In [3]:
#Replace all non-numeric characters in "Case numbers" column with zeroes.
data['Juhtumi nr'] = data['Juhtumi nr'].str.replace(pat=r'\D', repl='1', regex=True)
data.rename(columns={'Juhtumi nr' : 'Case'}, inplace=True)

#Convert to int64
data['Case'] = data['Case'].astype('int64')

#check
data['Case'].describe

<bound method NDFrame.describe of 0        2000140000057
1        2000140000067
2        2000140000123
3        2000140000235
4        2000150000442
             ...      
15703    3140170029504
15704    3140170029565
15705    3140170029903
15706    3140170029934
15707    1111180000018
Name: Case, Length: 15708, dtype: int64>

Fix 'Toimumisaeg'. separate dates and times to separate columns.

In [4]:
data["Date"], data["Time"] = data["Toimumisaeg"].str.split(" ", 1).str

data = data.drop("Toimumisaeg", axis=1)

#data['Time'] = pd.to_datetime(data['Time'], format='%H:%M').apply(pd.Timestamp).dt.time

print(data['Date'].describe)
print(data['Time'].describe)

<bound method NDFrame.describe of 0        24.10.2014
1        24.10.2014
2        08.11.2014
3        17.11.2014
4        28.04.2015
            ...    
15703    21.05.2017
15704    21.05.2017
15705    22.05.2017
15706    22.05.2017
15707    16.04.2018
Name: Date, Length: 15708, dtype: object>
<bound method NDFrame.describe of 0        08:45
1        13:45
2        15:10
3        17:32
4        07:55
         ...  
15703    09:35
15704    13:50
15705    18:29
15706    20:02
15707    16:20
Name: Time, Length: 15708, dtype: object>


C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\272288904.py:1: FutureWarning: In a future version of pandas all arguments of StringMethods.split except for the argument 'pat' will be keyword-only.
  data["Date"], data["Time"] = data["Toimumisaeg"].str.split(" ", 1).str
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\272288904.py:1: FutureWarning: Columnar iteration over characters will be deprecated in future releases.
  data["Date"], data["Time"] = data["Toimumisaeg"].str.split(" ", 1).str


Fix "isikuid".

In [5]:
#Rename column
data.rename(columns={'Isikuid' : 'Involved'}, inplace=True)

#Fix null/nan values
print("Count of null values: ", data['Involved'].isna().sum())
data.loc[data['Involved'].isna(), 'Involved'] = data['Hukkunuid'] + data['Vigastatuid']
data['Involved'].fillna(0, inplace=True)
print("Count of null values: ", data['Involved'].isna().sum())

#Set type as int64
data['Involved'] = data['Involved'].astype('int64', errors='ignore')

#check results
print(data['Involved'].value_counts(normalize=False, dropna=False))


Count of null values:  75
Count of null values:  0
2     8448
1     4680
3     1585
4      471
0      198
5      186
6       66
7       34
8       13
9        7
10       7
11       3
13       3
24       2
14       2
15       1
19       1
22       1
Name: Involved, dtype: int64


Fix "hukkunuid" and "vigastatuid".

In [6]:
data.rename(columns={'Hukkunuid' : 'Dead', 'Vigastatuid' : 'Wounded'}, inplace=True)

print(data['Dead'].value_counts(normalize=False, dropna=False))
print(data['Wounded'].value_counts(normalize=False, dropna=False))


0    14997
1      669
2       31
3        9
4        2
Name: Dead, dtype: int64
1     12679
2      1739
0       517
3       478
4       163
5        78
6        25
7         8
9         6
8         3
11        2
20        2
22        1
13        1
15        1
23        1
10        1
19        1
14        1
12        1
Name: Wounded, dtype: int64


Fix 'Sõidukeid':

In [7]:
#Rename column
data.rename(columns={'Sõidukeid' : 'Vehicles'}, inplace=True)

#Fill null values
data['Vehicles'].fillna(0, inplace=True)

#Fix type
data['Vehicles'] = data['Vehicles'].astype('int64', errors='ignore')

#Check
print(data['Vehicles'].value_counts(normalize=False, dropna=False))

1    8255
2    5575
3     977
0     655
4     179
5      46
6      16
7       4
9       1
Name: Vehicles, dtype: int64


Helper methods:

In [8]:
# Import the necessary modules
import requests
import json
import folium
from IPython.display import display
import pyproj
import time

COUNT_CONV = 0
COUNT_GPS = 0

def incrementConversions():
    global COUNT_CONV
    COUNT_CONV = COUNT_CONV + 1

def incrementCoords():
    global COUNT_GPS
    COUNT_GPS = COUNT_GPS + 1


def get_lat_lon(address):
    # Set up the URL template
    url = "https://nominatim.openstreetmap.org/search?format=json&q={}"

    # Replace spaces in the address with "+" characters
    address = address.replace(" ", "+")

    # Format the URL with the address
    url = url.format(address)

    # Send the request and get the response data
    response = requests.get(url)
    data = response.json()

    # Check if the data list is empty
    if not data:
        # If the data list is empty, return None
        return (None, None)

    # Extract the latitude and longitude from the response data
    lat = data[0]["lat"]
    lon = data[0]["lon"]

    # Return the latitude and longitude as a tuple
    incrementCoords()
    print(COUNT_GPS, lat, lon)
    return (lat, lon)


def show_map(lat, lon):
    # Import the necessary modules

    # Create a Map object
    m = folium.Map(location=[lat, lon], zoom_start=17)

    # Display the map
    display(m)


# Set up the L-EST97 projection using the pyproj.Proj class
l_est97 = pyproj.Proj(init='epsg:3301')
# Set up the WGS-84 projection using the pyproj.Proj class
wgs84 = pyproj.Proj(init='epsg:4326')
def convert_coordinates(x, y):
    # Convert the easting and northing coordinates from L-EST97 to WGS-84 using the pyproj.transform method
    lon, lat = pyproj.transform(l_est97, wgs84, y, x)

    incrementConversions()
    print(COUNT_CONV, "Old: ", x, y, " New: ", lat, lon)
    return lat, lon


def get_address(lat, lon):
    # Set up the URL template
    url = "https://nominatim.openstreetmap.org/reverse?format=json&lat={}&lon={}"

    # Format the URL with the latitude and longitude
    url = url.format(lat, lon)

    # Send the request and get the response data
    response = requests.get(url)
    data = response.json()

    # Extract the address from the response data
    address = data.get("display_name", "")

    time.sleep(1)

    # Return the address
    return address


def create_address(est_lat, est_lon):
    coords = convert_coordinates(est_lat, est_lon)

    #Create address from coords and return it.
    return get_address(coords[0], coords[1])


def update_lat_lon(row):
    # Convert the coordinates
    t = convert_coordinates(row['Latitude'], row['Longitude'])
    
    #Return converted coordinates as series
    return pd.Series({"Latitude": t[0], "Longitude": t[1]})


def update_lat_lon_from_address(address):
    #Get cords from address
    lat, lon = get_lat_lon(address)
    #return coords as a series
    return pd.Series({"Latitude": lat, "Longitude": lon})


c:\Users\Robert\miniconda3\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
c:\Users\Robert\miniconda3\lib\site-packages\pyproj\crs\crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
c:\Users\Robert\miniconda3\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change,

Example:

In [9]:
#Test getting cords of Delta Center
#coords = get_lat_lon('Narva mnt 18 51009 Tartu')
#print(coords[0], coords[1])
#show_map(coords[0], coords[1])

#The location should be: Harju maakond Tallinn Kesklinna linnaosa Estonia pst
x = 6588678.0	
y = 542647.0
cords = convert_coordinates(x, y)
print(cords)
show_map(cords[0], cords[1])

1 Old:  6588678.0 542647.0  New:  59.43379595290802 24.751478719314402
(59.43379595290802, 24.751478719314402)


C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)


Fix "Aadress PPA":

In [10]:
#Rename column
data.rename(columns={'Aadress (PPA)' : 'Address'}, inplace=True)


print("Count of null values in Address column pre modification: ", data['Address'].isnull().sum())

#Create a temp column we use to quantify rows
data.insert(1, "Temp", "")

#The ones with gps but no address can use gps as we use primarily gps in our project
data['Temp'] = np.where((data["GPS X"].notnull()) & (data["GPS Y"].notnull() & (data["Address"].isnull())), "ONLY GPS", data['Temp'])

#The ones without gps but with address can have their gps constructed
data['Temp'] = np.where((data["GPS X"].isnull()) & (data["GPS Y"].isnull() & (data["Address"].notnull())), "ONLY ADDRESS", data['Temp'])

#The ones without any location data will be dropped
data['Temp'] = np.where((data["GPS X"].isnull()) & (data["GPS Y"].isnull() & (data["Address"].isnull())), "NOTHING", data['Temp'])

print("Count of null values in Address column post modification: ", data['Address'].isnull().sum())
print()
print("Count of null values with only GPS data and no address: ", len(data[data['Temp'] == "ONLY GPS"]))
print("Count of rows with only Address data and no gps: ", len(data[data['Temp'] == "ONLY ADDRESS"]))
print("Count of null values with NO location data at all: ", len(data[data['Temp'] == "NOTHING"]))

print()

#Drop the rows with no location data
data = data[data['Temp'] != "NOTHING"]

#Adds addresses to the rows that have only gps
if generate_missing_address_from_coords_online:
    data.loc[data["Temp"] == "ONLY GPS", "Address"] = data.apply(lambda row: create_address(row["GPS X"], row["GPS Y"]), axis=1)
print("Count of null values in Address column post modification: ", data['Address'].isnull().sum())

#Drop the ones we could not generate and address for
data = data[data['Address'] != ""]

#Finally, remove any remaining rows where address remained null
data = data[pd.notnull(data['Address'])]


print("Count of null values in Address column after we drop the rows we could not get addresses for: ", data['Address'].isnull().sum())


Count of null values in Address column pre modification:  1107
Count of null values in Address column post modification:  1107

Count of null values with only GPS data and no address:  78
Count of rows with only Address data and no gps:  1215
Count of null values with NO location data at all:  1029

Count of null values in Address column post modification:  78
Count of null values in Address column after we drop the rows we could not get addresses for:  0


Fix "Liiklusõnnetuse liik [3]"

In [11]:
#Rename column
data.rename(columns={'Liiklusõnnetuse liik [3]' : 'Type'}, inplace=True)

print(data['Type'].value_counts(normalize=False, dropna=False))


Kokkupõrge jalakäijaga               3455
Kokkupõrge sõidukiga küljelt         2757
Sõiduki teelt väljasõit              2115
Kokkupõrge vastutuleva sõidukiga     1096
Kokkupõrge ees liikuva sõidukiga     1001
Sõiduki ümberpaiskumine teel          997
Kokkupõrge teevälise takistusega      852
Muu liiklusõnnetus                    652
Kokkupõrge ees seisva sõidukiga       559
Kukkumine ühissõidukis                486
Sõidukite külgkokkupõrge              273
Kokkupõrge loomaga                    162
Kokkupõrge teel oleva takistusega     111
Teadmata                               85
Name: Type, dtype: int64


Fixing the parttaker fields:

In [12]:
#Fix column names
data.rename(columns={
'Kergliikurijuhi osalusel' : 'Involved_lightmover',
'Jalakäija osalusel' : 'Involved_pedestrian',
'Kaassõitja osalusel' : 'Involved_passenger',
'Maastikusõiduki juhi osalusel' : 'Involved_offroad_vehicle',
'Eaka (65+) mootorsõidukijuhi osalusel' : 'Involved_elderly',
'Bussijuhi osalusel' : 'Involved_busdriver',
'Veoautojuhi osalusel' : 'Involved_truckdriver',
'Ühissõidukijuhi osalusel' : 'Involved_public_transport_driver',
'Sõiduautojuhi osalusel' : 'Involved_car_driver',
'Mootorratturi osalusel' : 'Involved_motorbike_driver',
'Mopeedijuhi osalusel' : 'Involved_moped_driver',
'Jalgratturi osalusel' : 'Involved_biker',
'Alaealise osalusel' : 'Involved_minor',
'Turvavarustust mitte kasutanud isiku osalusel' : 'Involved_not_wore_seatbelt',
'Esmase juhiloa omaniku osalusel' : 'Involved_learner_driver',
'Mootorsõidukijuhi osalusel' : 'Involved_vehicle_driver',
}, inplace=True)

cols = [
'Involved_lightmover',
'Involved_pedestrian',
'Involved_passenger',
'Involved_offroad_vehicle',
'Involved_elderly',
'Involved_busdriver',
'Involved_truckdriver',
'Involved_public_transport_driver',
'Involved_car_driver',
'Involved_motorbike_driver',
'Involved_moped_driver',
'Involved_biker',
'Involved_minor',
'Involved_not_wore_seatbelt',
'Involved_learner_driver',
'Involved_vehicle_driver']

#replace nans with 0-s, set all values to be if type int and remove any nan-s that might have popped up during that operation aswell
data[cols] = data[cols].replace(np.nan, 0)
data[cols] = data[cols].apply(pd.to_numeric, errors="coerce", downcast="integer")
data[cols] = data[cols].replace(np.nan, 0)

#verify results
for c in cols:
    print(data[c].value_counts(normalize=False, dropna=False))


0    14381
1      220
Name: Involved_lightmover, dtype: int64
0    11039
1     3562
Name: Involved_pedestrian, dtype: int64
0    10884
1     3717
Name: Involved_passenger, dtype: int64
0    14505
1       96
Name: Involved_offroad_vehicle, dtype: int64
0    12921
1     1680
Name: Involved_elderly, dtype: int64
0    13788
1      813
Name: Involved_busdriver, dtype: int64
0    13119
1     1482
Name: Involved_truckdriver, dtype: int64
0    13637
1      964
Name: Involved_public_transport_driver, dtype: int64
1    10445
0     4156
Name: Involved_car_driver, dtype: int64
0    13651
1      950
Name: Involved_motorbike_driver, dtype: int64
0    14060
1      541
Name: Involved_moped_driver, dtype: int64
0    12400
1     2201
Name: Involved_biker, dtype: int64
0    12119
1     2482
Name: Involved_minor, dtype: int64
0    12933
1     1668
Name: Involved_not_wore_seatbelt, dtype: int64
0    13384
1     1217
Name: Involved_learner_driver, dtype: int64
1    12782
0     1819
Name: Involved_vehicle_dr

Fix the road situation columns:

In [13]:
#Fix column names
data.rename(columns={
'Tee tüüp [2]':'Road_type',
'Tee element [1]':'Feature',
'Kurvilisus' : 'Curvature',
'Tee tasasus':'Levelness',
'Tee seisund':'Road_condition',
'Teekatte seisund [2]':'Surface_condition',
'Lubatud sõidukiirus (PPA)':'Speed_limit'
}, inplace=True)


cols = [
'Road_type',
'Feature',
'Curvature',
'Levelness',
'Road_condition',
'Surface_condition',
'Speed_limit'
]

#Set 0 speed limits as NaN as Estonia has no motorways without speed limits
data['Speed_limit'] = data['Speed_limit'].replace(0, np.nan)

#Fix a probable typo
data['Speed_limit'][data['Speed_limit'] == 901] = 90


#check results
print(data.shape)
print()
for c in cols:
    print(data[c].value_counts(normalize=False, dropna=False))
    print()

(14601, 37)

Tänav                    8059
Põhimaantee              1970
Kõrvalmaantee            1551
Tugimaantee              1132
Kohalik maantee           431
Muu koht                  331
Õuealatee                 299
Jalg- ja jalgrattatee     263
Parkla                    174
NaN                       124
Jalgtee                   112
Jalgrattatee               60
Väljak                     42
Metsatee                   31
Eramaantee                 17
Ramp, ühendustee            5
Name: Road_type, dtype: int64

Erielemendita teelõik    8649
Ristmik                  4463
Muu ristumine             629
NaN                       497
Kergliiklustee            191
Muu koht                  105
Parkla                     67
Name: Feature, dtype: int64

Sirge tee     12061
Lauge kurv     1700
NaN             427
Järsk kurv      413
Name: Curvature, dtype: int64

Tasane tee      13064
Kerge langus      616
Kerge tõus        422
NaN               360
Järsk langus       83
Järsk tõus      

C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\1836973779.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Speed_limit'][data['Speed_limit'] == 901] = 90


Fix weather and lighting:

In [14]:
#Fix column names
data.rename(columns={
'Ilmastik [1]':'Weather',
'Valgustus [2]':'Lighting'
}, inplace=True)


cols = ['Weather', 'Lighting']

#data = data.dropna(subset=cols)

#check results
print(data.shape)
print()
for c in cols:
    print(data[c].value_counts(normalize=False, dropna=False))
    print()

(14601, 37)

Selged olud                  7076
Pilvised olud                5681
Vihmasadu                     748
Lumised olud                  476
NaN                           274
Madal vastu paistev päike     215
Udused olud                   100
Tuisune või tormine            31
Name: Weather, dtype: int64

Valge aeg                        10310
Pimeda ajal valgustus põleb       2444
Pimeda ajal valgustus puudub      1331
Pimeda ajal valgustus ei põle      282
NaN                                234
Name: Lighting, dtype: int64



Fix gps:

In [15]:
#Fix column names
data.rename(columns={
'GPS X':'Latitude',
'GPS Y':'Longitude'
}, inplace=True)

print("Latitude nan count: ", data['Latitude'].isna().sum(), "Longitude nan count: ", data['Longitude'].isna().sum())

#first we must convert all we can, then create coords for the rows that have address, afterwards drop rest what we cant generate for

#Convert all coordinates from L-EST97 to WGS-84
if do_convert_coordinates:
    print("Now vonverting co-ordinates >>> ")
    data[["Latitude", "Longitude"]] = data.apply(update_lat_lon, axis=1)
    
    

#Try to generate missing coordinates from address data if permitted
if generate_missing_coords_from_address_online:
    print("Now generating co-ordinats from Address-es >>> ")
    #data[["Latitude", "Longitude"]] = data.apply(lambda row: update_lat_lon_from_address(row["Address"]), axis=1)
    # Select the rows where the "Temp" column has the value "ONLY ADDRESS", so we know which rows to try to create coords for
    rows = data.loc[data["Temp"] == "ONLY ADDRESS"]
    # Apply the update_lat_lon_from_address() function to the selected rows
    rows[["Latitude", "Longitude"]] = rows.apply(lambda row: update_lat_lon_from_address(row["Address"]), axis=1)
    data.update(rows)


#Finally remove any nan-s from rows where we did not generate coords from address or where generating was impossible
cols = ['Latitude', 'Longitude']
data = data.dropna(subset=cols)

Latitude nan count:  1215 Longitude nan count:  1220
Now vonverting co-ordinates >>> 


C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)


2 Old:  6588678.0 542647.0  New:  59.43379595290802 24.751478719314402
3 Old:  6589522.0 541467.0  New:  59.441488468586016 24.730849754494095
4 Old:  6593961.0 547646.0  New:  59.48068117988319 24.840723605498106
5 Old:  6569324.0 516628.0  New:  59.261884092987025 24.29152856115738
6 Old:  6586430.0 541953.0  New:  59.41368770550017 24.738814527574075
7 Old:  6576422.0 531951.0  New:  59.32472534488434 24.561208998955106
8 Old:  6575538.0 529034.0  New:  59.31699930958567 24.509856888443853
9 Old:  nan nan  New:  nan nan
10 Old:  6589152.0 546923.0  New:  59.43759881997651 24.82692138353671
11 Old:  6588079.0 544953.0  New:  59.428181385488976 24.791984228694364
12 Old:  6584974.0 539575.0  New:  59.4008472968574 24.696673492000393
13 Old:  6583421.0 538871.0  New:  59.38697273814087 24.684002458093488
14 Old:  6588058.0 542554.0  New:  59.4282403601292 24.749718009373705
15 Old:  6587832.0 544355.0  New:  59.42602735092067 24.781398902843076
16 Old:  6588441.0 541837.0  New:  59.431

C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


17 Old:  6590171.0 550290.0  New:  59.446358852285826 24.886488473768143
18 Old:  6581844.0 551674.0  New:  59.37145332578893 24.90889322342989


...

C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


14586 Old:  6588515.0 540718.0  New:  59.43252250180001 24.71745992820298
14587 Old:  6531825.0 550450.0  New:  58.92261274071956 24.87587946650629
14588 Old:  6502224.0 541648.0  New:  58.657814337732454 24.71758042867186
14589 Old:  6540259.0 545659.0  New:  58.99885945708304 24.794443608271962
14590 Old:  6472503.0 529740.0  New:  58.391958532266145 24.50853706632071
14591 Old:  6475350.0 528893.0  New:  58.41757617742631 24.494413199909285
14592 Old:  6585316.0 536154.0  New:  59.40422222337226 24.63651153787403
14593 Old:  6527767.0 418114.0  New:  58.88135642747581 22.579972689692795
14594 Old:  6435957.0 559125.0  New:  58.060880089861705 25.00161646419064
14595 Old:  6446219.0 553782.0  New:  58.15369275305819 24.913481575536974
14596 Old:  6462696.0 403412.0  New:  58.29427084775039 22.352818611023782


C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lon, lat = pyproj.transform(l_est97, wgs84, y, x)
C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\3866200897.py:66: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1


14597 Old:  6457753.0 408283.0  New:  58.250949113739004 22.437819090257758
14598 Old:  6480481.0 519847.0  New:  58.46414855123251 24.34006762403213
14599 Old:  6519056.0 524082.0  New:  58.810260868976385 24.416736737406524
14600 Old:  6558038.0 519643.0  New:  59.16044314701769 24.34337494890923
14601 Old:  nan nan  New:  nan nan
14602 Old:  6469176.0 592110.0  New:  58.353399543612305 25.57343534300201
Now generating co-ordinats from Address-es >>> 
1 59.4405533 24.8510036
2 59.4276122 24.6684541
3 59.4331163 24.7345346
4 58.08734325 27.10845127674058
5 58.88706225 25.569925618814434
6 59.4611157 24.6769259
7 59.442857 24.7399626
8 59.4592118 24.6690489
9 59.4143403 24.6906003
10 59.4023276 24.6972348
11 59.4331607 24.7615726
12 59.28056934999999 24.647138405082966
13 59.122980049999995 25.24112386680747
14 59.4329202 24.7460856
15 59.4613391 24.667202
16 59.4810982 24.8405704
17 59.4040341 24.6556211
18 59.4810982 24.8405704
19 59.4529605 24.7169552
20 59.3189028 24.5446487
21 59.

C:\Users\Robert\AppData\Local\Temp\ipykernel_5008\2582708464.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rows[["Latitude", "Longitude"]] = rows.apply(lambda row: update_lat_lon_from_address(row["Address"]), axis=1)


Remove temp column and drop any last nan rows, plus output the dataframe to a new csv file:

In [16]:
data.drop(['Temp'], axis=1, inplace=True)
#data.dropna(inplace=True)

data.to_csv('cleaned_data_file.csv', encoding='utf-8', index=False, header=True)

Final result:

In [19]:
print('Shape', data.shape)
print("Latitude nan count: ", data['Latitude'].isna().sum(), "Longitude nan count: ", data['Longitude'].isna().sum())
data.head()

Shape (14028, 36)
Latitude nan count:  0 Longitude nan count:  0


Case  Involved  Dead  Wounded  Vehicles  \
0  2.000140e+12       2.0   0.0      1.0       1.0   
1  2.000140e+12       2.0   0.0      1.0       2.0   
2  2.000140e+12       2.0   0.0      1.0       2.0   
3  2.000140e+12       2.0   0.0      2.0       2.0   
4  2.000150e+12       2.0   0.0      1.0       2.0   

                                             Address  \
0   Harju maakond Tallinn Kesklinna linnaosa Esto...   
1   Harju maakond Tallinn Põhja-Tallinna linnaosa...   
2   Harju maakond Tallinn Pirita linnaosa Meriväl...   
3                         Harju maakond Keila vald     
4   Harju maakond Tallinn Kesklinna linnaosa Pärn...   

                               Type  Involved_lightmover  Involved_pedestrian  \
0            Kokkupõrge jalakäijaga                  0.0                  1.0   
1  Kokkupõrge ees liikuva sõidukiga                  0.0                  0.0   
2  Kokkupõrge ees liikuva sõidukiga                  0.0                  0.0   
3  Kokkupõrge vastutuleva sõidukiga                  0.0                  0.0   
4      Kokkupõrge sõidukiga küljelt                  0.0                  0.0   

   Involved_passenger  ...   Levelness      Road_condition  Surface_condition  \
0                 0.0  ...  Tasane tee  Sõidutee on korras               Kuiv   
1                 0.0  ...  Tasane tee  Sõidutee on korras               Kuiv   
2                 0.0  ...  Tasane tee  Sõidutee on korras               Kuiv   
3                 1.0  ...  Tasane tee  Sõidutee on korras               Kuiv   
4                 0.0  ...  Tasane tee  Sõidutee on korras               Märg   

   Speed_limit        Weather                       Lighting   Latitude  \
0         50.0    Selged olud                      Valge aeg  59.433796   
1         30.0  Pilvised olud                      Valge aeg  59.441488   
2         50.0  Pilvised olud                      Valge aeg  59.480681   
3         90.0  Pilvised olud  Pimeda ajal valgustus ei põle  59.261884   
4         50.0      Vihmasadu                      Valge aeg  59.413688   

   Longitude        Date   Time  
0  24.751479  24.10.2014  08:45  
1   24.73085  24.10.2014  13:45  
2  24.840724  08.11.2014  15:10  
3  24.291529  17.11.2014  17:32  
4  24.738815  28.04.2015  07:55  

[5 rows x 36 columns]